In [ ]:
from keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, InputLayer, BatchNormalization, Dropout, Activation
from sagemaker.tensorflow import TensorFlow
from keras.models import Sequential
from keras.datasets import cifar10
from keras.utils import np_utils
from tensorflow import keras
import tensorflow as tf
import argparse, os
import numpy as np
import sagemaker
import random
import boto3
import keras
import time
import os

In [1]:
print(sagemaker.__version__)

sess = sagemaker.Session()
role = sagemaker.get_execution_role()

2.107.0



## Download the cifar10 dataset

In [2]:

(x_train, y_train), (x_val, y_val) = cifar10.load_data()

os.makedirs("./data", exist_ok = True)

np.savez('./data/training', image=x_train, label=y_train)
np.savez('./data/validation', image=x_val, label=y_val)


In [3]:
# print training and validation shape & unique values
print('x_train shape:', x_train.shape)
print(x_train.shape[0], 'train samples')
print(x_val.shape[0], 'Validation samples')
num_classes=len(np.unique(y_train))
print(f'num of classes = {num_classes}')

x_train shape: (50000, 3, 32, 32)
50000 train samples
10000 Validation samples
num of classes = 10


# Save Data in s3 Bucket

In [4]:
prefix = 'tf2-Cifar-10'

# training_input_path   = sess.upload_data('data/training.npz', key_prefix=prefix+'/training')
# validation_input_path = sess.upload_data('data/validation.npz', key_prefix=prefix+'/validation')
training_input_path = 's3://sagemaker-us-east-1-436756716598/tf2-Cifar-10/training/training.npz'
validation_input_path = 's3://sagemaker-us-east-1-436756716598/tf2-Cifar-10/validation/validation.npz'
print(training_input_path)
print(validation_input_path)

s3://sagemaker-us-east-1-436756716598/tf2-Cifar-10/training/training.npz
s3://sagemaker-us-east-1-436756716598/tf2-Cifar-10/validation/validation.npz


# Train with Tensorflow 

In [1]:
env = {
    'SAGEMAKER_REQUIREMENTS': 'requirements.txt', # path relative to `source_dir` below.
}

hyperparameters={'epochs': 20,
                 'batch-size': 32} 

simple_tf_estimator = TensorFlow(entry_point='train.py',
                          source_dir='src',
                          role=role,
                          instance_count=1, 
                          instance_type='ml.m5.xlarge',     # $0.922 per hours
                          framework_version='2.3', 
                          py_version='py37',
                          script_mode=True,
                          hyperparameters = hyperparameters)

NameError: name 'TensorFlow' is not defined

In [6]:
simple_tf_estimator.hyperparameters()

{'epochs': '20', 'batch-size': '32', 'model_dir': 'null'}

In [13]:
simple_tf_estimator.fit({'training': training_input_path, 'validation': validation_input_path})

2022-09-04 10:02:09 Starting - Starting the training job...
2022-09-04 10:02:29 Starting - Preparing the instances for trainingProfilerReport-1662285729: InProgress
......
2022-09-04 10:03:37 Downloading - Downloading input data...
2022-09-04 10:04:08 Training - Downloading the training image...
2022-09-04 10:04:38 Training - Training image download completed. Training in progress..2022-09-04 10:04:41.330783: W tensorflow/core/profiler/internal/smprofiler_timeline.cc:460] Initializing the SageMaker Profiler.
2022-09-04 10:04:41.334334: W tensorflow/core/profiler/internal/smprofiler_timeline.cc:105] SageMaker Profiler is not enabled. The timeline writer thread will not be started, future recorded events will be dropped.
2022-09-04 10:04:41.495906: W tensorflow/core/profiler/internal/smprofiler_timeline.cc:460] Initializing the SageMaker Profiler.
2022-09-04 10:04:44,763 sagemaker-training-toolkit INFO     Imported framework sagemaker_tensorflow_container.training
2022-09-04 10:04:44,771

# Deploy in Prodection

In [14]:
tf_endpoint_name = 'keras-tf-fmnist-'+time.strftime("%Y-%m-%d-%H-%M-%S", time.gmtime())

tf_predictor = simple_tf_estimator.deploy(
                 initial_instance_count=1, 
                 instance_type='ml.m5.large',
                 endpoint_name=tf_endpoint_name)

update_endpoint is a no-op in sagemaker>=2.
See: https://sagemaker.readthedocs.io/en/stable/v2.html for details.


-----!

# prediction

In [15]:
x_test = 'data/validation.npz'
num_samples = 10

In [16]:
%matplotlib inline
num_samples = 5
indices = random.sample(range(x_val.shape[0] - 1), num_samples)
images = x_val[indices]/255
labels = y_val[indices]

payload = images.reshape(num_samples, 3, 32, 32)

In [17]:
response = tf_predictor.predict(payload)

prediction = np.array(response['predictions'])
predicted_label = prediction.argmax(axis=1)
print('Predicted labels are: {}'.format(predicted_label))

Predicted labels are: [1 6 9 8 3]


In [19]:
class_names = ['airplane',
'automobile',
'bird',
'cat',
'deer',
'dog',
'frog',
'horse',
'ship',
'truck']

In [25]:
class_names

['airplane',
 'automobile',
 'bird',
 'cat',
 'deer',
 'dog',
 'frog',
 'horse',
 'ship',
 'truck']

In [38]:
for i in range (5):
    a= [class_names[i] for i in predicted_label]

In [42]:
# classes start from zero-Nine(0-9)
print('All Cifar-10 Classes are:: {}'.format(class_names))
print('Predicted Score are: {}'.format(predicted_label))
print('Predicted labels are: {}'.format(a))

All Cifar-10 Classes are:: ['airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck']
Predicted Score are: [1 6 9 8 3]
Predicted labels are: ['automobile', 'frog', 'truck', 'ship', 'cat']


# Delete Endpoint

In [47]:

# tf_endpoint_name.delete_endpoint()
bucket_to_delete = boto3.resource('s3').Bucket('sagemaker-us-east-1-436756716598')
bucket_to_delete.objects.all().delete()

[{'ResponseMetadata': {'RequestId': '8YGXEM51MAS6J639',
   'HostId': 'cPTFVP7JJOoAbRCDlC5vQA9dwaYCJ9s39e9GyKvqpxknFhkoWkkv9kNR7fs3C8CB9JH3FdM+uZM=',
   'HTTPStatusCode': 200,
   'HTTPHeaders': {'x-amz-id-2': 'cPTFVP7JJOoAbRCDlC5vQA9dwaYCJ9s39e9GyKvqpxknFhkoWkkv9kNR7fs3C8CB9JH3FdM+uZM=',
    'x-amz-request-id': '8YGXEM51MAS6J639',
    'date': 'Sun, 04 Sep 2022 11:00:47 GMT',
    'content-type': 'application/xml',
    'transfer-encoding': 'chunked',
    'server': 'AmazonS3',
    'connection': 'close'},
   'RetryAttempts': 0},
  'Deleted': [{'Key': 'tensorflow-training-2022-09-04-08-15-07-128/rule-output/ProfilerReport-1662279307/profiler-output/profiler-reports/Dataloader.json'},
   {'Key': 'tensorflow-training-2022-09-04-09-35-18-586/rule-output/ProfilerReport-1662284118/profiler-output/profiler-reports/OverallSystemUsage.json'},
   {'Key': 'tensorflow-training-2022-09-04-10-02-09-774/rule-output/ProfilerReport-1662285729/profiler-output/profiler-reports/IOBottleneck.json'},
   {'Key': 

In [49]:
# tf_predictor.delete_endpoint()